### Load libraries and external data

In [1]:
%load_ext autoreload
%autoreload 2

In [2]:
from data import dataloader
import json
from neuralnet import nn
import numpy as np
import pixiedust_node

Pixiedust database opened successfully


#### Load data from Firebase.
Requires [Firebase service account credentials](https://console.firebase.google.com/project/tingle-pilot-collected-data/settings/serviceaccounts/adminsdk) in JSON format saved in `./firebase-credentials`.

In [3]:
pilot_data = dataloader.break_out_blocks(
    dataloader.load_from_firebase()
)

pixiedust_node 0.2.5 started. Cells starting '%%node' may contain Node.js code.
Data loaded from Firebase!


In [10]:
pilot_data.columns

Index(['distance', 'hand', 'ontarget', 'pitch', 'question', 'roll', 'section',
       'step', 'target', 'thermopile1', 'thermopile2', 'thermopile3',
       'thermopile4', 'timestamp', 'human-readable timestamp',
       'iteration_block'],
      dtype='object')

#### Load [Synaptic](http://caza.la/synaptic/)

In [4]:
%%node
var synaptic = require('synaptic');
var Neuron = synaptic.Neuron,
  Layer = synaptic.Layer,
  Network = synaptic.Network,
  Trainer = synaptic.Trainer,
  Architect = synaptic.Architect;

... ... ... ...


Define Perceptron and associated functions

In [5]:
%%node
/**
 * @constructor {function} Perceptron - Function to create synaptic perceptron
 * @see https://github.com/cazala/synaptic/blob/master/README.md
 * @param input
 * @param hidden
 * @param output
 * @this
 */
function Perceptron(input, hidden, output){
  // create the layers
  var inputLayer = new Layer(input);
  var hiddenLayer = new Layer(hidden);
  var outputLayer = new Layer(output);

  // connect the layers
  inputLayer.project(hiddenLayer);
  hiddenLayer.project(outputLayer);

  // set the layers
  this.set({
    input: inputLayer,
    hidden: [hiddenLayer],
    output: outputLayer
  });
}

// extend the prototype chain
Perceptron.prototype = new Network();
Perceptron.prototype.constructor = Perceptron;


/**
 * @function runPerceptronOnList - Function to run a perceptron on an
 * Array of Numeric input Arrays and return an Array of Numeric output Arrays.
 * @parameter {Perceptron} perceptron
 * @parameter {Numeric[][]} listOfInputs
 * @returns {Numeric[][]}
 */
function runPerceptronOnList(perceptron, listOfInputs){
  var outputs = [];
  for(var i=0; i<listOfInputs.length; i++){
    outputs.push(perceptron.activate(listOfInputs[i]));
  }
  return(outputs);
}

... ... ... ... ... ... ...
... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ...
... ... ... ... ... ...
... ... ..... ..... ... ...


---
### See all targets, number of available samples and iteration blocks

In [6]:
for target in list(pilot_data.target.unique()):
    ib =max(
        pilot_data.loc[
            pilot_data.target==target
        ].iteration_block.dropna()
    )
    print(": ".join([
        target,
        "{0} on-target samples in {1} iteration block{2}".format(
            str(len(pilot_data.loc[
                (pilot_data.target == target) &
                (pilot_data.ontarget)
            ])),
            "%.0f" % ib,
            "s" if ib != 1 else ""
        )
    ]))

none: 19 on-target samples in 2 iteration blocks
environment: 106 on-target samples in 4 iteration blocks
body: 101 on-target samples in 2 iteration blocks
cup: 33 on-target samples in 3 iteration blocks
food: 35 on-target samples in 4 iteration blocks
nails: 69 on-target samples in 3 iteration blocks
smoke: 92 on-target samples in 3 iteration blocks
eyebrow: 235 on-target samples in 5 iteration blocks
nose: 249 on-target samples in 4 iteration blocks
above-ear: 403 on-target samples in 5 iteration blocks
behind-ear: 220 on-target samples in 4 iteration blocks
opposite-cheek: 74 on-target samples in 6 iteration blocks
chin: 166 on-target samples in 1 iteration block
cheek: 686 on-target samples in 6 iteration blocks
forehead: 176 on-target samples in 1 iteration block
top-head: 160 on-target samples in 1 iteration block
back-head: 170 on-target samples in 1 iteration block
opposite-face: 381 on-target samples in 2 iteration blocks
paint-mouth: 81 on-target samples in 3 iteration blocks

---
### Extract training and testing data
Define targets of interest and corresponding offtargets

In [7]:
with open(
    'data/targets.json',
    'r'
) as fp:
    targets = json.load(
        fp
    )[0]

Get training inputs and outputs, inputs that should evaluate ~true and inputs that should evaluate ~false

In [19]:
data = {}
for target in targets:
    data[target] = {
        "train": nn.define_trainer_data(
            pilot_data,
            {
                "target": [target],
                "offtarget": targets[target]
            },
            [
                "distance",
                "thermopile1",
                "thermopile2",
                "thermopile3",
                "thermopile4"
            ],
            list(range(1, 7)),
            100
        ),
        "test_true": nn.define_activation(
            pilot_data,
            [target],
            [
                "distance",
                "thermopile1",
                "thermopile2",
                "thermopile3",
                "thermopile4"
            ],
            list(range(1, 7)),
            exclude=100
        ),
        "test_false": nn.define_activation(
            pilot_data,
            targets[target],
            [
                "distance",
                "thermopile1",
                "thermopile2",
                "thermopile3",
                "thermopile4"
            ],
            list(range(1, 7)),
            exclude=100
        )
    }

Preview all inputs and training outputs

In [20]:
data

{'above-ear': {'test_false': [[0.0,
    0.8183760683760684,
    0.8719646799116998,
    0.8660812294182219,
    0.8551042810098793],
   [0.0,
    0.8162393162393163,
    0.8719646799116998,
    0.8507135016465424,
    0.8375411635565313],
   [0.0,
    0.811965811965812,
    0.870860927152318,
    0.8342480790340286,
    0.8342480790340286],
   [0.0,
    0.811965811965812,
    0.858719646799117,
    0.8441273326015369,
    0.8441273326015369],
   [0.0,
    0.8205128205128205,
    0.8664459161147904,
    0.8562019758507136,
    0.8616904500548848],
   [0.0,
    0.8322649572649574,
    0.8730684326710817,
    0.8496158068057081,
    0.8616904500548848],
   [0.6095617529880478,
    0.8376068376068377,
    0.9061810154525386,
    0.8957189901207464,
    0.8902305159165752],
   [0.0,
    0.8429487179487181,
    0.9061810154525386,
    0.9088913282107575,
    0.8792535675082327],
   [0.09163346613545817,
    0.8429487179487181,
    0.9094922737306844,
    0.9055982436882547,
    0.87925356750

**Note**: These data take some time to copy across environments. Give the notebook some time between running cells across Python and JavaScript.

---
### Train and test

In [21]:
%%node
var test_outputs = {};
for(var target in data){
  var perceptron5 = new Perceptron(5,5,5,5,1);
  var perceptron7 = new Perceptron(5,7,7,7,7,7,1);
  var trainer5 = new Trainer(perceptron5);
  var trainer7 = new Trainer(perceptron7);
  test_outputs[target] = {
    "true": {
      "5": [],
      "7": []
    },
    "false": {
      "5": [],
      "7": []
    }
  };
  for(var iteration=0; iteration < data[target]["train"].length; iteration++){
    trainer5.train({
      "input": data[target]["train"][iteration]["input"],
      "output": data[target]["train"][iteration]["output"]
    });
    trainer7.train({
      "input": data[target]["train"][iteration]["input"],
      "output": data[target]["train"][iteration]["output"]
    });
  }
  for(var iteration=0; iteration < data[target]["test_true"].length; iteration++){
    test_outputs[target]["true"]["5"].push(perceptron5.activate(data[target]["test_true"][iteration]));
    test_outputs[target]["true"]["7"].push(perceptron7.activate(data[target]["test_true"][iteration]));
  }
  for(var iteration=0; iteration < data[target]["test_false"].length; iteration++){
    test_outputs[target]["false"]["5"].push(perceptron5.activate(data[target]["test_false"][iteration]));
    test_outputs[target]["false"]["7"].push(perceptron7.activate(data[target]["test_false"][iteration]));
  }
}

... ... ... ... ... ..... ....... ....... ....... ..... ....... ....... ....... ..... ... ..... ....... ....... ....... ..... ....... ....... ....... ..... ... ..... ..... ..... ... ..... ..... ..... ...


---
### See outputs

If the training is adequate x ≈ 0 ∀ x in the following:

In [22]:
f = [
    *[
        np.mean(output['5']) for output in [
            outputs['false'] for outputs in [
                test_outputs[i] for i in test_outputs
            ]
        ] if len(output['5'])
    ],
    *[
        np.mean(output['7']) for output in [
            outputs['false'] for outputs in [
                test_outputs[i] for i in test_outputs
            ]
        ] if len(output['7'])
    ]
]
f

[0.5013462078339748,
 0.5063313058428094,
 0.500680689875387,
 0.5060085692018778,
 0.500281191214067,
 0.5013160202285049,
 0.5083141219611105,
 0.49633458587139956,
 0.49885413930016503,
 0.49870222199246994,
 0.5000934208148814,
 0.4886914107062965,
 0.5043009967528771,
 0.5035826548039377,
 0.5074608782839334,
 0.5008036596061671,
 0.49385396240830165,
 0.5003421299173266,
 0.5018511294926545,
 0.49655255585715863,
 0.5161647351061858,
 0.5048655049857635,
 0.5109453341254924,
 0.48719099379498026,
 0.5030591695512621,
 0.49804954810552876]

If the training is adequate x ≈ 1 ∀ x in the following:

In [23]:
t = [
    *[
        np.mean(output['5']) for output in [
            outputs['true'] for outputs in [
                test_outputs[i] for i in test_outputs
            ]
        ] if len(output['5'])
    ],
    *[
        np.mean(output['7']) for output in [
            outputs['true'] for outputs in [
                test_outputs[i] for i in test_outputs
            ]
        ] if len(output['7'])
    ]
]
t

[0.5007098220308909,
 0.5060418718730539,
 0.5002612437258218,
 0.5012651093878365,
 0.49633859968009475,
 0.4988889253301214,
 0.4986866893431937,
 0.5001047401759993,
 0.4887046791315197,
 0.5043069618778453,
 0.5008785523641421,
 0.49393900766782467,
 0.5002890422338244,
 0.5018437320281358,
 0.5162244454787137,
 0.5049201687223872,
 0.5109838231199082,
 0.4871943544407394,
 0.5030105542485575,
 0.49809126687028804]

Finally, if training is adequate, f ≪ t:

In [ ]:
f_mean = np.mean(f)
t_mean = np.mean(t)
print(
    "f = {0}\nt = {1}\n{0} ≪ {1} ?".format(
        str(f_mean),
        str(t_mean)
    ) if f_mean < t_mean else "Nope. f > t"
)

---
### Try with demo data

In [ ]:
with open(
    'data/demo_data.json',
    'r'
) as fp:
    demo_data = json.load(
        fp
    )[0]

In [ ]:
scale = 98.6
demo_test = {
    "train":[
        *[{
            "input": [
                float(d)/scale for d in datum[0:4]
            ],
            "output": 1.0
        } for datum in demo_data["true"][0:25]],
        *[{
            "input": [
                float(d)/scale for d in datum[0:4]
            ],
            "output": 0.0
        } for datum in demo_data["false"][0:25]]
    ],
    "test_true": [[
                float(d)/scale for d in datum[0:4]
            ] for datum in demo_data["true"][26:]],
    "test_false": [[
                float(d)/scale for d in datum[0:4]
            ] for datum in demo_data["false"][26:]]
}

In [ ]:
demo_test

In [ ]:
%%node
var test_outputs = {};
var perceptron5 = new Perceptron(5,5,5,5,1);
var perceptron7 = new Perceptron(5,7,7,7,7,7,1);
var trainer5 = new Trainer(perceptron5);
var trainer7 = new Trainer(perceptron7);
demo_test_outputs = {
"true": {
  "5": [],
  "7": []
},
"false": {
  "5": [],
  "7": []
}
};
for(var iteration=0; iteration < demo_test["train"].length; iteration++){
trainer5.train({
  "input": demo_test["train"][iteration]["input"],
  "output": demo_test["train"][iteration]["output"]
});
trainer7.train({
  "input": demo_test["train"][iteration]["input"],
  "output": demo_test["train"][iteration]["output"]
});
}
for(var iteration=0; iteration < demo_test["test_true"].length; iteration++){
demo_test_outputs["true"]["5"].push(perceptron5.activate(demo_test["test_true"][iteration]));
demo_test_outputs["true"]["7"].push(perceptron7.activate(demo_test["test_true"][iteration]));
}
for(var iteration=0; iteration < demo_test["test_false"].length; iteration++){
demo_test_outputs["false"]["5"].push(perceptron5.activate(demo_test["test_false"][iteration]));
demo_test_outputs["false"]["7"].push(perceptron7.activate(demo_test["test_false"][iteration]));
}

In [ ]:
scale = 1
demo_test = {
    "train":[
        *[{
            "input": [
                float(d)/scale for d in datum[0:4]
            ],
            "output": 1.0
        } for datum in demo_data["true"][0:25]],
        *[{
            "input": [
                float(d)/scale for d in datum[0:4]
            ],
            "output": 0.0
        } for datum in demo_data["false"][0:25]]
    ],
    "test_true": [[
                float(d)/scale for d in datum[0:4]
            ] for datum in demo_data["true"][26:]],
    "test_false": [[
                float(d)/scale for d in datum[0:4]
            ] for datum in demo_data["false"][26:]]
}

In [ ]:
demo_test

In [ ]:
%%node
var test_outputs = {};
var perceptron5 = new Perceptron(4,5,5,5,1);
var perceptron7 = new Perceptron(4,7,7,7,7,7,1);
var trainer5 = new Trainer(perceptron5);
var trainer7 = new Trainer(perceptron7);
demo_test_outputs = {
"true": {
  "5": [],
  "7": []
},
"false": {
  "5": [],
  "7": []
}
};
for(var iteration=0; iteration < demo_test["train"].length; iteration++){
trainer5.train({
  "input": demo_test["train"][iteration]["input"],
  "output": demo_test["train"][iteration]["output"]
});
trainer7.train({
  "input": demo_test["train"][iteration]["input"],
  "output": demo_test["train"][iteration]["output"]
});
}
for(var iteration=0; iteration < demo_test["test_true"].length; iteration++){
demo_test_outputs["true"]["5"].push(perceptron5.activate(demo_test["test_true"][iteration]));
demo_test_outputs["true"]["7"].push(perceptron7.activate(demo_test["test_true"][iteration]));
}
for(var iteration=0; iteration < demo_test["test_false"].length; iteration++){
demo_test_outputs["false"]["5"].push(perceptron5.activate(demo_test["test_false"][iteration]));
demo_test_outputs["false"]["7"].push(perceptron7.activate(demo_test["test_false"][iteration]));
}

In [ ]:
demo_test_outputs

---
code from https://github.com/ChildMindInstitute/tingle-gesture-recognition-pilot-toolkit/blob/master/full/js/app-web-bluetooth.js

In [24]:
%%node
// ************** NEURAL NET #1
var Neuron = synaptic.Neuron;
var Layer = synaptic.Layer;
var Network = synaptic.Network;
var Trainer = synaptic.Trainer;
var Architect = synaptic.Architect;
var neuralNet = new Architect.LSTM(7, 5, 2, 1);
var trainer = new Trainer(neuralNet);
var trainingData;



// ************* NEURAL NET #2
var Neuron2 = synaptic.Neuron;
var Layer2 = synaptic.Layer;
var Network2 = synaptic.Network;
var Trainer2 = synaptic.Trainer;
var Architect2 = synaptic.Architect;
var neuralNet2 = new Architect2.LSTM(5, 5, 2, 1);
var trainer2 = new Trainer2(neuralNet2);
var trainingData2;


function getNNScore(selectNN) {

    var scoreArray = new Array(1).fill(0);
    var timeStamp = new Date().getTime();
    var displayScore;

    if (selectNN == 1) {
        if (NN1NumInputs == 5) {
            var feedArray = new Array(5).fill(0);
        } else if (NN1NumInputs == 7) {
            var feedArray = new Array(7).fill(0);
        } else if (NN1NumInputs == 2) {
            var feedArray = new Array(2).fill(0);
        }
        if (NN1NumInputs == 5 || NN1NumInputs == 7) {
            feedArray[0] = sensorDataArray[0] / 101;
            feedArray[1] = sensorDataArray[1] / 101;
            feedArray[2] = sensorDataArray[2] / 101;
            feedArray[3] = sensorDataArray[3] / 101;

            feedArray[4] = sensorDataArray[4] / 250;
            //     feedArray[4] = sensorDataArray[4] / 450;
        }

        if (NN1NumInputs == 7) {
            feedArray[5] = sensorDataArray[5] / 360;
            feedArray[6] = sensorDataArray[6] / 360;
        }

        if (NN1NumInputs == 2) {
            feedArray[0] = sensorDataArray[5] / 360;
            feedArray[1] = sensorDataArray[6] / 360;
        }

        // use trained NN or loaded NN
        if (haveNNFlag1 && activeNNFlag1) {
            scoreArray = neuralNet.activate(feedArray);
        } else if (loadNNFlag) {
            scoreArray = neuralNetwork1(feedArray);
        }
        console.log("NN1 FEED ARRAY: " + feedArray);
        console.log("NN1 SCORE ARRAY: " + scoreArray);

        displayScore = scoreArray[0].toFixed(4) * 100;
        displayScore = displayScore.toFixed(2);
        $(".message-nn1-score").html(displayScore + '%');
        var rawLineNN1Chart = scoreArray[0].toFixed(4);
        rawLineNN1Chart = (rawLineNN1Chart / 3) + 0.8;
        lineNN1.append(timeStamp, rawLineNN1Chart);

    } else if (selectNN == 2) {
        if (NN2NumInputs == 5) {
            var feedArray = new Array(5).fill(0);
        } else if (NN2NumInputs == 7) {
            var feedArray = new Array(7).fill(0);
        } else if (NN2mInputs == 2) {
            var feedArray = new Array(2).fill(0);
        }
        if (NN2NumInputs == 5 || NN2NumInputs == 7) {
            feedArray[0] = sensorDataArray[0] / 101;
            feedArray[1] = sensorDataArray[1] / 101;
            feedArray[2] = sensorDataArray[2] / 101;
            feedArray[3] = sensorDataArray[3] / 101;

            feedArray[4] = sensorDataArray[4] / 250;
            //  feedArray[4] = sensorDataArray[4] / 450;
        }

        if (NN2NumInputs == 7) {
            feedArray[5] = sensorDataArray[5] / 360;
            feedArray[6] = sensorDataArray[6] / 360;
        }

        if (NN2NumInputs == 2) {
            feedArray[0] = sensorDataArray[5] / 360;
            feedArray[1] = sensorDataArray[6] / 360;
        }

        if (haveNNFlag2 && activeNNFlag2) {
            scoreArray = neuralNet2.activate(feedArray);
        } else if (loadNNFlag) {
            scoreArray = neuralNetwork2(feedArray);
        }

        console.log("NN2 FEED ARRAY: " + feedArray);
        console.log("NN2 SCORE ARRAY: " + scoreArray);

        displayScore = scoreArray[0].toFixed(4) * 100;
        displayScore = displayScore.toFixed(2);
        $(".message-nn2-score").html(displayScore + '%');
        var rawLineNN2Chart = scoreArray[0].toFixed(4);
        rawLineNN2Chart = (rawLineNN2Chart / 3) + 0.8;
        lineNN2.append(timeStamp, rawLineNN2Chart);
    }

}



/**************************** TRAIN NN ******************************/
function trainNN(selectNN) {
    //'5:2:1', '5:5:1', '5:5:2:1', '5:5:5:1', '7:2:1', '7:7:1', '7:7:2:1', '7:7:7:1'
    //  var processedDataSession = sensorDataSession;
    var processedDataSession = new Array;
    var falseDataArray = new Array;
    var trueDataArray = new Array;

    trainingData = new Array;

    var rawNNArchitecture = $(".range-slider__value.nn-architecture").html();
    var numInputs = parseInt(rawNNArchitecture.charAt(0));

    nnRate = $("#rate-input").val();
    nnIterations = $("#iterations-input").val();
    nnError = $("#error-input").val();

    if (selectNN == 1) {
        trueDataArray = NN1TrueDataArray;
        falseDataArray = NN1FalseDataArray;
    } else if (selectNN == 2) {
        trueDataArray = NN2TrueDataArray;
        falseDataArray = NN2FalseDataArray;
    }

    //combine true and false data
    var addSample = new Array(13).fill(0);

    for (var j = 0; j < trueDataArray.length; j++) {
        addSample = trueDataArray[j];
        addSample[12] = 1; //true
        processedDataSession.push(addSample);
    }
    for (var k = 0; k < falseDataArray.length; k++) {
        addSample = falseDataArray[k];
        addSample[12] = 0; //false
        processedDataSession.push(addSample);
    }


    //   console.log("raw NN architecture: " + rawNNArchitecture);

    if (selectNN == 1) {
        NN1Architecture = rawNNArchitecture;
    } else {
        NN2Architecture = rawNNArchitecture;
    }

    if (rawNNArchitecture == '5:2:1') {
        if (selectNN == 1) {
            neuralNet = new Architect.LSTM(5, 2, 1);
        } else {
            neuralNet2 = new Architect2.LSTM(5, 2, 1);
        }
    } else if (rawNNArchitecture == '5:5:1') {
        if (selectNN == 1) {
            neuralNet = new Architect.LSTM(5, 5, 1);
        } else {
            neuralNet2 = new Architect2.LSTM(5, 5, 1);
        }
    } else if (rawNNArchitecture == '5:5:2:1') {
        if (selectNN == 1) {
            neuralNet = new Architect.LSTM(5, 5, 2, 1);
        } else {
            neuralNet2 = new Architect2.LSTM(5, 5, 2, 1);
        }
    } else if (rawNNArchitecture == '5:5:5:1') {
        if (selectNN == 1) {
            neuralNet = new Architect.LSTM(5, 5, 5, 1);
        } else {
            neuralNet2 = new Architect2.LSTM(5, 5, 5, 1);
        }
    } else if (rawNNArchitecture == '7:7:1') {
        if (selectNN == 1) {
            neuralNet = new Architect.LSTM(7, 7, 1);
        } else {
            neuralNet2 = new Architect2.LSTM(7, 7, 1);
        }
    } else if (rawNNArchitecture == '7:5:2:1') {
        if (selectNN == 1) {
            neuralNet = new Architect.LSTM(7, 5, 2, 1);
        } else {
            neuralNet2 = new Architect2.LSTM(7, 5, 2, 1);
        }
    } else if (rawNNArchitecture == '7:7:2:1') {
        if (selectNN == 1) {
            neuralNet = new Architect.LSTM(7, 7, 2, 1);
        } else {
            neuralNet2 = new Architect2.LSTM(7, 7, 2, 1);
        }
    } else if (rawNNArchitecture == '7:7:7:1') {
        if (selectNN == 1) {
            neuralNet = new Architect.LSTM(7, 7, 7, 1);
        } else {
            neuralNet2 = new Architect2.LSTM(7, 7, 7, 1);
        }
    } else if (rawNNArchitecture == '2:2:2:1') {
        if (selectNN == 1) {
            neuralNet = new Architect.LSTM(2, 2, 2, 1);
        } else {
            neuralNet2 = new Architect2.LSTM(2, 2, 2, 1);
        }
    }

    if (selectNN == 1) {
        NN1Architecture = rawNNArchitecture;
        NN1NumInputs = numInputs;
        trainer = new Trainer(neuralNet);
    } else {
        NN2Architecture = rawNNArchitecture;
        NN2NumInputs = numInputs;
        trainer2 = new Trainer2(neuralNet2);
    }

    // var minMaxAreaSize = processedDataSession.length * 0.01; //sample edge size for average min or max over that area
    //  console.log("SIZE OF UNPROCESSED SESSION DATA: " + processedDataSession.length);


    for (var i = 0; i < processedDataSession.length; i++) {

        var currentSample = processedDataSession[i];
        var outputArray = new Array(1).fill(0);

        outputArray[0] = currentSample[12]; //true or false

        if (numInputs == 5) {

            var inputArray = new Array(5).fill(0);
            inputArray[0] = currentSample[0] / 101;
            inputArray[1] = currentSample[1] / 101;
            inputArray[2] = currentSample[2] / 101;
            inputArray[3] = currentSample[3] / 101;
            inputArray[4] = currentSample[4] / 250;

        } else if (numInputs == 7) {

            var inputArray = new Array(7).fill(0);
            inputArray[0] = currentSample[0] / 101;
            inputArray[1] = currentSample[1] / 101;
            inputArray[2] = currentSample[2] / 101;
            inputArray[3] = currentSample[3] / 101;
            inputArray[4] = currentSample[4] / 250;
            inputArray[5] = currentSample[5] / 360;
            inputArray[6] = currentSample[6] / 360;

        } else if (numInputs == 2) {

            var inputArray = new Array(2).fill(0);
            inputArray[0] = currentSample[5] / 360;
            inputArray[1] = currentSample[6] / 360;
        }


        trainingData.push({
            input: inputArray,
            output: outputArray
        });

        console.log(currentSample + " TRAINING INPUT: " + inputArray + "  --> NN# " + selectNN);
        console.log(currentSample + " TRAINING OUTPUT: " + outputArray + "  --> NN# " + selectNN);
    }


    if (selectNN == 1) {
        console.log("TRAINING ON selectNN1 --> interations:" + nnIterations + "  error:" + nnError + "  rate:" + nnRate + "  arch:" + rawNNArchitecture + "  inputs:" + numInputs);

        trainer.train(trainingData, {
            rate: nnRate,
            //   iterations: 15000,
            iterations: nnIterations,
            error: nnError,
            shuffle: true,
            //   log: 1000,
            log: 5,
            cost: Trainer.cost.CROSS_ENTROPY
        });

        //we have a trained NN to use
        haveNNFlag1 = true;
        trainNNFlag1 = false;
        $('#activate-btn').addClass("haveNN");
        $('#export-btn').addClass("haveNN");

    } else if (selectNN == 2) {
        console.log("TRAINING ON selectNN2");

        trainer2.train(trainingData, {
            rate: nnRate,
            //   iterations: 15000,
            iterations: nnIterations,
            error: nnError,
            shuffle: true,
            //   log: 1000,
            log: 5,
            cost: Trainer2.cost.CROSS_ENTROPY
        });

        //we have a trained NN to use
        haveNNFlag2 = true;
        trainNNFlag2 = false;
        $('#activate2-btn').addClass("haveNN");
        $('#export2-btn').addClass("haveNN");
    }

}

... ... ... ... ... ... ... ..... ..... ..... ..... ..... ..... ... ..... ..... ..... ..... ..... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ...
... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ..... ..... ..... ..... ... ... ..... ..... ..... ..... ... ... ..... ..... ..... ..... ... ... ..... ..... ..... ..... ... ... ..... ..... ..... ..... ... ... ..... ..... ..... ..... ... ... ..... ..... ..... ..... ... ... ..... ..... ..... ..... ... ... ..... ..... ..... ..... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ..